# 使用 TVM nn.module 工作流在 MLC-LLM 中添加新模型架构

在本教程中，将演示如何使用新的 TVM nn.module 工作流在 MLC-LLM 中添加新模型架构。TVM nn.module 是新的模型编译工作流，旨在为 MLC-LLM 带来模块化的 Python 优先编译，使用户和开发者能够更无缝地支持新模型和功能。

例如，在 TVM nn.module 工作流下，定义 Mistral 模型架构所需的代码量仅为旧工作流的一半左右。从高层次来看，TVM nn.module 与 PyTorch nn.module 接口非常相似。

在这里，将使用 [GPT-2](https://huggingface.co/gpt2) 进行演示。GPT-2 是以自监督方式在非常大的英语语料库上预训练的 transformers 模型，可用于猜测句子中的下一个单词。它在 Huggingface 中的[模型定义](https://github.com/huggingface/transformers/blob/main/src/transformers/models/gpt2/modeling_gpt2.py)可以找到。

## 定义 GPT-2 模型

在 `mlc-llm/python/mlc_llm/model/` 下创建 `gpt2` 文件夹。其结构将如下所示：

```
mlc-llm/python/mlc_llm/model/gpt2/
├── gpt2_loader.py          # 从 Huggingface 加载并转换权重
├── gpt2_model.py           # 定义模型架构和配置
├── gpt2_quantization.py    # 定义量化方案
└── __init__.py
```

首先关注 `gpt2_model.py`。该文件使用 `tvm.relax.frontend.nn.Module` 以模块化的方式定义 GPT-2 模型架构，类似于 PyTorch 的对应部分。

In [1]:
from set_env import temp_dir

### 在 `gpt2_model.py` 中定义配置类

首先，定义配置类，它几乎是从 Huggingface 的 [GPT2Config](https://github.com/huggingface/transformers/blob/main/src/transformers/models/gpt2/configuration_gpt2.py) 直接翻译过来的。该类的属性应与 Huggingface 配置中的相应属性同名，否则 Huggingface 配置将无法正确加载。

`__post_init__` 函数在所有数据类属性初始化后被调用。

In [2]:
from mlc_llm.model.gpt2.gpt2_model import GPT2Config

GPT2Config??

Init signature:
GPT2Config(
    vocab_size: int,
    n_embd: int,
    n_layer: int,
    n_head: int,
    layer_norm_epsilon: float,
    n_inner: int = -1,
    context_window_size: int = 0,
    prefill_chunk_size: int = 0,
    scale_attn_by_inverse_layer_idx: bool = False,
    tensor_parallel_shards: int = 1,
    head_dim: int = 0,
    max_batch_size: int = 1,
    kwargs: Dict[str, Any] = <factory>,
) -> None
Source:        
@dataclasses.dataclass
class GPT2Config(ConfigBase):  # pylint: disable=too-many-instance-attributes
    """Configuration of the GPT-2 model."""

    vocab_size: int
    n_embd: int
    n_layer: int
    n_head: int
    layer_norm_epsilon: float
    n_inner: int = -1
    context_window_size: int = 0
    prefill_chunk_size: int = 0
    scale_attn_by_inverse_layer_idx: bool = False
    tensor_parallel_shards: int = 1
    head_dim: int = 0
    max_batch_size: int = 1
    kwargs: Dict[str, Any] = dataclasses.field(default_factory=dict)

    def __post_init__(self):
     

### 在 `gpt2_model.py` 中定义模型架构

使用 {class}`tvm.relax.frontend.nn.Module`，能够以模块化的方式定义模型架构。它看起来与 PyTorch 风格非常相似，只是前向函数实际上并不执行计算。它使用作为输入传递的占位符来跟踪计算图。

你可以选择使用 `op._print(some_tensor)` 在运行编译模块时打印张量的中间值。如果你这样做，你必须在 `export_tvm()` 和 `jit()` 中指定 `debug=True`。除了手动打印外，还提供了[端到端的调试模块 `DebugChat`](#Debug-Compiled-MLC-Model-with-DebugChat)，它将自动转储所有层的中间值。

In [3]:
from mlc_llm.model.gpt2.gpt2_model import GPT2Attention
GPT2Attention??

Init signature: GPT2Attention(config: mlc_llm.model.gpt2.gpt2_model.GPT2Config)
Docstring:     
Base class for neural network components. Subclass it to build your models.
Modules can nest within each other in a tree structure using regular attribute assignment.
Source:        
class GPT2Attention(nn.Module):  # pylint: disable=too-many-instance-attributes
    def __init__(self, config: GPT2Config):
        self.embed_dim = config.n_embd
        if config.n_head % config.tensor_parallel_shards != 0:
            raise ValueError(
                f"Cannot split {config.n_head} attention heads "
                f"evenly to {config.tensor_parallel_shards} GPUs."
            )
        self.num_heads = config.n_head // config.tensor_parallel_shards
        self.head_dim = config.head_dim
        self.scale_attn_by_inverse_layer_idx = config.scale_attn_by_inverse_layer_idx

        self.c_attn = nn.Linear(
            in_features=self.embed_dim,
            out_features=3 * self.num_heads * s

请注意，已经提供了一些内置的常用模块，你会发现它们非常方便。例如，这里的 `nn.Linear` 和 `nn.KVCache` 模块都是 MLC-LLM 中的[内置模块](https://github.com/apache/tvm/blob/unity/python/tvm/relax/frontend/nn/modules.py)。

同样，也提供了许多常见的对张量进行操作的[内置算子](https://github.com/apache/tvm/blob/unity/python/tvm/relax/frontend/nn/op.py)。例如，`op.reshape`、`op.matmul`、`op.softmax` 等。

### 使用 `nn.spec` 定义模型规范

一旦验证了模型的每一层行为正确，就可以编写模型规范，将模型从 `nn.module` 转换为 TVM IRModule。

在 `get_default_spec` 函数中，需要定义如下模型规范：

In [4]:
from mlc_llm.model.gpt2.gpt2_model import GPT2LMHeadModel

GPT2LMHeadModel.get_default_spec??

Signature: GPT2LMHeadModel.get_default_spec(self)
Docstring: <no docstring>
Source:   
    def get_default_spec(self):
        mod_spec = {
            "embed": {
                "input_ids": nn.spec.Tensor(["seq_len"], "int32"),
                "$": {
                    "param_mode": "packed",
                    "effect_mode": "none",
                },
            },
            "prefill": {
                "input_embed": nn.spec.Tensor([1, "seq_len", self.n_embed], self.dtype),
                "paged_kv_cache": nn.spec.Object(object_type=PagedKVCache),
                "$": {
                    "param_mode": "packed",
                    "effect_mode": "none",
                },
            },
            "decode": {
                "input_embed": nn.spec.Tensor([1, 1, self.n_embed], self.dtype),
                "paged_kv_cache": nn.spec.Object(object_type=PagedKVCache),
                "$": {
                    "param_mode": "packed",
                    "effect_mode": "none",
 

所有指定的方法，例如 `embed`、`prefill`、`decode` 等，都将被导出到 TVM IRModule 中。支持 `nn.spec.Tensor`、`nn.spec.Tuple` 和整数作为 relax 函数的输入。

"default" 和 "packed" 调用约定之间的区别如下：![](images/diff.png)

在提供模型规范后，可以使用 `export_tvm` 函数轻松地将 TVM nn.module 转换为 relax Tensor IR。可以查看整个模型的 Tensor IR 表示，以及模型参数名称和数据类型的完整列表。

In [5]:
from mlc_llm.model.gpt2 import gpt2_model

config_dict = {
    "architectures": ["GPT2LMHeadModel"],
    "bos_token_id": 50256,
    "eos_token_id": 50256,
    "hidden_act": "gelu_new",
    "n_ctx": 1024,
    "n_embd": 768,
    "n_head": 12,
    "n_layer": 12,
    "n_positions": 1024,
    "layer_norm_epsilon": 1e-05,
    "scale_attn_by_inverse_layer_idx": False,
    "vocab_size": 50257,
}

config = gpt2_model.GPT2Config.from_dict(config_dict)
model = gpt2_model.GPT2LMHeadModel(config)
mod, named_params = model.export_tvm(
    spec=model.get_default_spec(),
)

# Uncomment the following line to show the model in Tensor IR
# mod.show(black_format=False)

for name, param in named_params:
    print(name, param.shape, param.dtype)

transformer.wte.weight [vocab_size, 768] float32
transformer.wpe.weight [1024, 768] float32
transformer.h.0.ln_1.weight [768] float32
transformer.h.0.ln_1.bias [768] float32
transformer.h.0.attn.c_attn.weight [2304, 768] float32
transformer.h.0.attn.c_attn.bias [2304] float32
transformer.h.0.attn.c_proj.weight [768, 768] float32
transformer.h.0.attn.c_proj.bias [768] float32
transformer.h.0.ln_2.weight [768] float32
transformer.h.0.ln_2.bias [768] float32
transformer.h.0.mlp.c_fc.weight [3072, 768] float32
transformer.h.0.mlp.c_fc.bias [3072] float32
transformer.h.0.mlp.c_proj.weight [768, 3072] float32
transformer.h.0.mlp.c_proj.bias [768] float32
transformer.h.1.ln_1.weight [768] float32
transformer.h.1.ln_1.bias [768] float32
transformer.h.1.attn.c_attn.weight [2304, 768] float32
transformer.h.1.attn.c_attn.bias [2304] float32
transformer.h.1.attn.c_proj.weight [768, 768] float32
transformer.h.1.attn.c_proj.bias [768] float32
transformer.h.1.ln_2.weight [768] float32
transformer.h.1

### 在 `gpt2_loader.py` 中定义加载器

在 `gpt2_loader.py` 中，定义了如何将 Huggingface 的参数转换为 MLC 模型所使用的格式。

加载器类将返回 [`ExternMapping`](https://github.com/mlc-ai/mlc-llm/blob/main/python/mlc_llm/loader/mapping.py)，其中包含两种映射：
- **源 -> MLC 参数映射**：例如参数重命名、参数转换等。
- **未使用的映射**：源中未在 MLC 模型定义中使用的参数。

在 GPT-2 中，由于使用了 Conv1D，需要对 `c_attn`、`c_proj` 和 `c_fc` 的权重进行转置。为此，将提供映射函数，如下所示：

```python
for conv1d_weight_name in ["attn.c_attn", "attn.c_proj", "mlp.c_proj", "mlp.c_fc"]:
    src_name = f"h.{i}.{conv1d_weight_name}.weight"
    mlc_name = f"transformer.{src_name}"
    mapping.add_mapping(
        mlc_name,
        [src_name],
        functools.partial(
            lambda x, dtype: x.transpose().astype(dtype),
            dtype=named_parameters[mlc_name].dtype,
        ),
    )
```

为了使 GPT-2 参数转换正常工作，还需要进行一些重命名操作。请参考[gpt2_loader.py](https://github.com/mlc-ai/mlc-llm/blob/main/python/mlc_llm/model/gpt2/gpt2_loader.py)。



## 将模型添加到支持的预构建模型工作流

一旦整个模型在 TVM 的 `nn.module` 中定义完毕，包括模型架构、模型加载器和模型量化器，就可以将其添加到支持的预构建模型工作流中。

在[`mlc-llm/python/mlc_llm/model/model.py`](https://github.com/mlc-ai/mlc-llm/blob/main/python/mlc_llm/model/model.py)中，将GPT-2模型添加到 `MODELS` 列表中：

```python
"gpt2": Model(
    name="gpt2",
    model=gpt2_model.GPT2LMHeadModel,
    config=gpt2_model.GPT2Config,
    source={
        "huggingface-torch": gpt2_loader.huggingface,
        "huggingface-safetensor": gpt2_loader.huggingface,
    },
    quantize={
        "no-quant": gpt2_quantization.no_quant,
        "group-quant": gpt2_quantization.group_quant,
    },
)
```

## 编译 GPT-2 模型库和权重

以下步骤与[通用模型编译工作流](https://llm.mlc.ai/docs/compilation/compile_models.html)相同。

In [13]:
# Create directory
!mkdir -p {temp_dir}/dist/models
%cd {temp_dir}/dist/models

# Clone HF weights
!git lfs install
# git clone https://huggingface.co/openai-community/gpt2
# git clone git@hf.co:openai-community/gpt2
!git clone https://hf-mirror.com/openai-community/gpt2
%cd ../..

/media/pc/data/lxw/ai/tvm-book/tests/.temp/dist/models
Updated git hooks.
Git LFS initialized.
正克隆到 'gpt2'...
remote: Enumerating objects: 87, done.
remote: Counting objects: 100% (3/3), done.
remote: Compressing objects: 100% (2/2), done.
remote: Total 87 (delta 0), reused 0 (delta 0), pack-reused 84 (from 1)
展开对象中: 100% (87/87), 1.65 MiB | 38.00 KiB/s, 完成.
过滤内容: 100% (11/11), 5.23 GiB | 2.64 MiB/s, 完成.
/media/pc/data/lxw/ai/tvm-book/tests/.temp


In [15]:
# Convert weight
!python -m mlc_llm convert_weight {temp_dir}/dist/models/gpt2/ --device cuda --quantization q0f16 -o {temp_dir}/dist/gpt2-q0f16-MLC

[2025-01-07 11:11:43] INFO auto_config.py:116: Found model configuration: /media/pc/data/lxw/ai/tvm-book/tests/.temp/dist/models/gpt2/config.json
[2025-01-07 11:11:46] INFO auto_device.py:79: Found device: cuda:0
[2025-01-07 11:11:46] INFO auto_device.py:79: Found device: cuda:1
[2025-01-07 11:11:46] INFO auto_weight.py:71: Finding weights in: /media/pc/data/lxw/ai/tvm-book/tests/.temp/dist/models/gpt2
[2025-01-07 11:11:46] INFO auto_weight.py:130: Found source weight format: huggingface-torch. Source configuration: /media/pc/data/lxw/ai/tvm-book/tests/.temp/dist/models/gpt2/pytorch_model.bin
[2025-01-07 11:11:49] INFO auto_weight.py:161: Found source weight format: huggingface-safetensor. Source configuration: /media/pc/data/lxw/ai/tvm-book/tests/.temp/dist/models/gpt2/model.safetensors.index.json
[2025-01-07 11:11:49] INFO auto_weight.py:107: Using source weight configuration: /media/pc/data/lxw/ai/tvm-book/tests/.temp/dist/models/gpt2/pytorch_model.bin. Use `--source` to override.
[

1. gen_config: 生成 `mlc-chat-config.json` 并处理分词器

In [17]:
!python -m mlc_llm gen_config {temp_dir}/dist/models/gpt2 --quantization q0f16 --conv-template gpt2 -o {temp_dir}/dist/gpt2-q0f16-MLC/

[2025-01-07 11:12:41] INFO auto_config.py:116: Found model configuration: /media/pc/data/lxw/ai/tvm-book/tests/.temp/dist/models/gpt2/config.json
[2025-01-07 11:12:41] INFO auto_config.py:154: Found model type: gpt2. Use `--model-type` to override.
[2025-01-07 11:12:41] INFO gpt2_model.py:47: context_window_size not found in config.json. Falling back to n_positions (1024)
[2025-01-07 11:12:41] INFO gpt2_model.py:64: prefill_chunk_size defaults to 1024
[2025-01-07 11:12:41] INFO config.py:107: Overriding max_batch_size from 1 to 128
[2025-01-07 11:12:41] INFO gen_config.py:150: [generation_config.json] Setting bos_token_id: 50256
[2025-01-07 11:12:41] INFO gen_config.py:150: [generation_config.json] Setting eos_token_id: 50256
[2025-01-07 11:12:41] INFO gen_config.py:164: Not found tokenizer config: /media/pc/data/lxw/ai/tvm-book/tests/.temp/dist/models/gpt2/tokenizer.model
[2025-01-07 11:12:41] INFO gen_config.py:162: Found tokenizer config: /media/pc/data/lxw/ai/tvm-book/tests/.temp/d

2. 编译：根据 `mlc-chat-config.json` 中的规范编译模型库

In [18]:
!python -m mlc_llm compile {temp_dir}/dist/gpt2-q0f16-MLC/mlc-chat-config.json --device cuda -o {temp_dir}/dist/gpt2-q0f16-MLC/gpt2-q0f16-cuda.so

[2025-01-07 11:13:02] INFO auto_config.py:70: Found model configuration: /media/pc/data/lxw/ai/tvm-book/tests/.temp/dist/gpt2-q0f16-MLC/mlc-chat-config.json
[2025-01-07 11:13:05] INFO auto_device.py:79: Found device: cuda:0
[2025-01-07 11:13:05] INFO auto_device.py:79: Found device: cuda:1
[2025-01-07 11:13:05] INFO auto_target.py:78: Found configuration of target device "cuda:0": {"thread_warp_size": runtime.BoxInt(32), "arch": "sm_86", "max_threads_per_block": runtime.BoxInt(1024), "max_num_threads": runtime.BoxInt(1024), "kind": "cuda", "max_shared_memory_per_block": runtime.BoxInt(49152), "tag": "", "keys": ["cuda", "gpu"]}
[2025-01-07 11:13:05] INFO auto_target.py:110: Found host LLVM triple: x86_64-unknown-linux-gnu
[2025-01-07 11:13:05] INFO auto_target.py:111: Found host LLVM CPU: haswell
[2025-01-07 11:13:05] INFO auto_target.py:334: Generating code for CUDA architecture: sm_86
[2025-01-07 11:13:05] INFO auto_target.py:335: To produce multi-arch fatbin, set environment variabl

(Debug-Compiled-MLC-Model-with-DebugChat)=
## 使用 DebugChat 调试编译的 MLC 模型

在成功编译模型库并转换模型权重后，检查模型是否生成正确的输出非常重要。一种检查方法是在相同的输入 tokens 下，将模型的输出 logits 与其 Huggingface PyTorch 版本的输出进行比较。

为了帮助调试 MLC 模型，提供了 `mlc_llm.testing.DebugChat` 模块，该模块可以：

- 加载刚刚编译的 MLC 模型
- 使用用户指定的 prompt 运行模型的完整 `forward` 流程
- 转储所有层的中间值。

然后，您可以将这些中间值与 Huggingface PyTorch 模型的中间值进行比较。（对于 PyTorch，您可以使用 [`register_forward_hook`](https://pytorch.org/docs/stable/generated/torch.nn.Module.html#torch.nn.Module.register_forward_hook) 提取中间值。）

In [20]:
!python -m mlc_llm.testing.debug_chat --model {temp_dir}/dist/gpt2-q0f16-MLC/ --model-lib {temp_dir}/dist/gpt2-q0f16-MLC/gpt2-q0f16-cuda.so --device cuda --debug-dir {temp_dir}/debug-gpt2 --generate-len 5 "Hey how are you doing today?"

Traceback (most recent call last):
  File "<frozen runpy>", line 198, in _run_module_as_main
  File "<frozen runpy>", line 88, in _run_code
  File "/media/pc/data/lxw/ai/mlc-llm/python/mlc_llm/testing/debug_chat.py", line 536, in <module>
    main()
  File "/media/pc/data/lxw/ai/mlc-llm/python/mlc_llm/testing/debug_chat.py", line 523, in main
    dc = DebugChat(
         ^^^^^^^^^^
  File "/media/pc/data/lxw/ai/mlc-llm/python/mlc_llm/testing/debug_chat.py", line 227, in __init__
    self.mod, self.params, self.metadata = _get_tvm_module(
                                           ^^^^^^^^^^^^^^^^
  File "/media/pc/data/lxw/ai/mlc-llm/python/mlc_llm/testing/debug_chat.py", line 49, in _get_tvm_module
    ex = tvm.runtime.load_module(lib_path)
         ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/media/pc/data/lxw/ai/tvm/python/tvm/runtime/module.py", line 683, in load_module
    raise ValueError(f"cannot find file {path}")
ValueError: cannot find file /media/pc/data/lxw/ai/tvm-book/tests/

中间输出会被转储到 `debug-gpt2` 文件夹中。对于每个 prefill/decode 阶段，都有单独的文件夹，其中包含存储每个内核函数调用参数的 `.npz` 文件。

例如：`./debug-gpt2/decode_2/f0_take3.npz` 对应第 2 个解码步骤中的第 0 个 `take` 函数调用。输出 logits 会保存到 `logits.npz` 中。

**注意**：由于 TIR 函数调用采用[目标传递风格](https://mlc.ai/chapter_end_to_end/index.html#call-dps-packed-construct)，每个函数调用的参数会如下所示：

```python
def low_level_prim_func(in0, in1, ..., out):
    # 实现
```

因此，函数调用的最后一个参数将是输出。

`.npz` 文件可以按以下方式加载：

In [21]:
import numpy as np

data = np.load(f'{temp_dir}/debug-gpt2/decode_2/f0_take3.npz')
print(data)
print(data["arg_0"])
print(data["arg_1"])
print(data["arg_2"]) # This is the output of the take function

FileNotFoundError: [Errno 2] No such file or directory: '/media/pc/data/lxw/ai/tvm-book/tests/.temp/debug-gpt2/decode_2/f0_take3.npz'